In [1]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException
import selenium.common.exceptions as sex

import pandas as pd
import numpy as np

from bs4 import BeautifulSoup
import lxml

import time
from time import sleep
import random
import re

In [2]:
df = pd.read_csv('base_dataset.csv', index_col=0)
df.head()


name      address        specification  \
4                 잎사귀치과병원  서울 서대문구 신촌동            진료중\n야간진료   
1                 라이크치과의원   서울 마포구 대흥동            진료중\n야간진료   
3  한국건강관리협회 건강증진의원 서울서부지부  서울 강서구 화곡6동                  진료중   
0                  콤비치과의원     서울 중구 명동  진료중\n야간진료\n전문의\n여의사   
5              관악연세공감치과의원  서울 관악구 낙성대동  진료중\n야간진료\n전문의\n여의사   

                                                link  stars  reviews  
4  https://www.modoodoc.com/hospital/140/%EC%9E%8...    8.3      247  
1  https://www.modoodoc.com/hospital/4139/%EB%9D%...    9.0      204  
3  https://www.modoodoc.com/hospital/3575/%ED%95%...    8.8      192  
0  https://www.modoodoc.com/hospital/114/%EC%BD%A...    9.6      173  
5  https://www.modoodoc.com/hospital/473/%EA%B4%8...    9.0      146

In [61]:
df.reviews.unique()

array([247, 204, 192, 173, 146, 142, 141, 120, 115, 113, 110, 107, 106,
       101,  93,  91,  90,  88,  87,  78,  77,  74,  73,  70,  69,  66,
        64,  63,  59,  58,  57,  55,  54,  53,  52,  51,  50,  47,  46,
        45,  43,  42,  41,  40,  39,  38,  37,  36,  35,  34,  33,  32,
        31,  30,  29,  28,  27,  26,  25,  24,  23,  22,  21,  20,  19,
        18,  17,  16,  15,  14,  13,  12,  11,  10,   9,   8,   7,   6,
         5,   4,   3,   2,   1], dtype=int64)

In [118]:
work_df = df[df['reviews']<100]
work_df.reviews.unique()
work_df = work_df[work_df['reviews']>9]
work_df = work_df[work_df['reviews']<21]
work_df.reviews.unique()

array([20, 19, 18, 17, 16, 15, 14, 13, 12, 11, 10], dtype=int64)

In [11]:
path = "C:\\chromedriver.exe"
driver = webdriver.Chrome(path)
driver.implicitly_wait(5)

start_url = 'https://www.modoodoc.com/hospital/114/%EC%BD%A4%EB%B9%84%EC%B9%98%EA%B3%BC%EC%9D%98%EC%9B%90-%EC%84%9C%EC%9A%B8%EC%8B%9C-%EC%A4%91%EA%B5%AC-%EB%AA%85%EB%8F%992%EA%B0%80/'
driver.get(start_url)

C:\Users\yukir\AppData\Local\Temp/ipykernel_29936/2478835588.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(path)


In [122]:
root_url = work_df.link.tolist()
print(len(root_url))

urls_list=[]

for j in root_url:
    root_url = j
    
    for i in range(1,3):
#         print(root_url)
        urls = root_url+('?page='+str(i))
        urls_list.append(urls)
        print(urls)
        
print(len(urls_list))

807
https://www.modoodoc.com/hospital/1524/%EC%84%9C%EC%9A%B8e%EC%B9%98%EA%B3%BC%EC%9D%98%EC%9B%90-%EC%84%9C%EC%9A%B8%EC%8B%9C-%EA%B5%AC%EB%A1%9C%EA%B5%AC-%EC%98%A4%EB%A5%98%EB%8F%99/?page=1
https://www.modoodoc.com/hospital/1524/%EC%84%9C%EC%9A%B8e%EC%B9%98%EA%B3%BC%EC%9D%98%EC%9B%90-%EC%84%9C%EC%9A%B8%EC%8B%9C-%EA%B5%AC%EB%A1%9C%EA%B5%AC-%EC%98%A4%EB%A5%98%EB%8F%99/?page=2
https://www.modoodoc.com/hospital/44225/%EC%9D%B4%EC%97%98%EC%B9%98%EA%B3%BC%EB%B3%91%EC%9B%90-%EB%8C%80%EC%A0%84-%EC%8B%A0%ED%83%84%EC%A7%84%EB%8F%99/?page=1
https://www.modoodoc.com/hospital/44225/%EC%9D%B4%EC%97%98%EC%B9%98%EA%B3%BC%EB%B3%91%EC%9B%90-%EB%8C%80%EC%A0%84-%EC%8B%A0%ED%83%84%EC%A7%84%EB%8F%99/?page=2
https://www.modoodoc.com/hospital/1351/%EB%B3%B4%EC%8A%A4%ED%86%A4%ED%83%91%EC%B9%98%EA%B3%BC%EC%9D%98%EC%9B%90-%EC%84%9C%EC%9A%B8%EC%8B%9C-%EC%9D%80%ED%8F%89%EA%B5%AC-%EB%8C%80%EC%A1%B0%EB%8F%99/?page=1
https://www.modoodoc.com/hospital/1351/%EB%B3%B4%EC%8A%A4%ED%86%A4%ED%83%91%EC%B9%98%EA%B3%BC%EC%9D%

In [123]:
reviews = []
stars= []
hoss = []
treatments=[]
addr = []


z=0
j=0

for i in urls_list:
#     j=0
#     print(i)
    driver.get(i)
    driver.implicitly_wait(5)
    page = driver.page_source
    soup = BeautifulSoup(page, 'html.parser')
    
    
    hos = soup.find_all('h1', class_="my-1 hospital-doctor-name-box d-flex align-items-center")
    for i in hos:
        hos = i.text
        hos = hos.strip()
        print('\n>>>>>>>>>>>>>>       {}      <<<<<<<<<<<<<<'.format(hos))
        hoss.append(hos)

    adr = soup.find_all('div', class_="color49 mt-3")
    for i in adr:
        i = i.text
        i = i.strip()
        addr.append(i)
        print(i)
    
    
    review = soup.find_all('div', class_="toast-message content-box text-left class49 mb-4 pb-2") 
    for i in review:
        text = i.text
        #     print(text)
        text = text.replace('\n', '')
        text = text.replace('                        ', '')
        text = text.replace('                    ', '')
        z+=1
        print(str(z)+' //'+hos+'// '+text)
#         print("reviews extracted")
        reviews.append(str(z)+' //'+hos+'// '+text)
        

    star = soup.find_all('span', class_ = "h-100 align-bottom")   
    for i in star:
        i = i.text
        i=i.strip()
        stars.append(i)
        print(i)
    # print("Star/ed")
    
    
    treatment = soup.find_all('div', class_="text-left mt-2 title-box")
    for i in treatment:
        treat = i.text
        treat = treat.replace(' ','')
        treat = treat.replace('\n','')
        treat = treat.split(':')[1]
        treatments.append(treat)
        print(treat)
        
    j+=1
    
    print('------------     남은 페이지수 {}     ----------------'.format(len(urls_list)-j))
    
    x = random.randint(0,2)
    sleep(x)
            
    print('ㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇ sleep for {} ㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇㅇ'.format(x))


>>>>>>>>>>>>>>       서울e치과의원      <<<<<<<<<<<<<<
서울특별시 구로구 천왕로 106 (오류동) (천왕역 1번 출구 바로 앞)
1 //서울e치과의원// 과잉진료 하지 않는 동네 치과입니다.이빨도 떼울거 안떼울거 구분해서 알려주세요.그냥 약간 썩고있으면 치료 안해줍니다.그대신 담에 방문했을때 치료할만하면 또 치료해줘요.대기도 별로 없어서 좋아요.
2 //서울e치과의원// 직원들이 친절한 느낌은 아니지만 그렇다고 불편하지도 않아요. 딱 좋아요~~ 설명도 잘 해주십니다^^ 사랑니가 4개 있는데 이곳에서 총 3개 뺏습니다. 아프지 않게 잘 해주셔요. 남은 하나도 여기서 뽑으려고요~~
3 //서울e치과의원// 충치 치료를 위해 방문했고 상담받았을 때까지는 좋았어요.신경치료를 받아야 된다고 하셨고 서약서에 싸인을 하라고 하셨죠.3~5회정도 받을꺼하고 하셨어요. 금 45 지르코니아 45 PFM 35였구요.일단 예약이 너~~무 힘들어요. 천왕역 치과 중에선 유일하게 야간진료가하루 목요일에 있는데 거의 full로 차있어요. 토욜도 마찬가지구요.집근처라 편하려고 진료를 시작했는데 직장인인 저는 예약 잡아서 원하는날짜와 시간에 진료 받기가 너무 힘드네요. 그래서 반차나 연차 쓰면서받아야 돼요. 미리 선예약도 안되더라구요. 그럼 환자들은 계속해서 예약을할꺼고 저는 매번 평일 오전이나 낮에 진료를 받아야 된다는건데 그냥 차라리회사 근처로 할껄 싶더라구요. 그랬으면 점심시간이라도 갔을테니깐요.그 점 말고는 아직까지는 무난히 괜찮은 곳이라는 판단입니당
4 //서울e치과의원// 충치 치료를 위해 상담을 받았어요. 사진도 찍고 했는데 인레이를 받았던 곳이 많이 썩어서신경치료 및 크라운 치료를 받아야 된다고 하더라구요.천왕역 치과 4군데를 다녀왔는데 여기가 제일 저렴하고친절하고 깔끔하며 과잉진료 없이 좋았던 것 같아요.충치 상담을 위해 든 비용은 10,800원 이구요.인레이 기본은 20, 금은 30 이고 PFM 크라운은 35금 크라운은 45 지르코니아 크라

In [125]:
import pickle
with open ('reviews.pkl','wb') as f:
    pickle.dump(reviews, f)

with open ('stars.pkl','wb') as f:
    pickle.dump(stars, f)

with open ('treatments.pkl','wb') as f:
    pickle.dump(treatments, f)

with open ('addr.pkl','wb') as f:
    pickle.dump(addr, f)
    
with open('reviews.pkl', 'rb') as f:
    reviews_check = pickle.load(f)

with open('stars.pkl', 'rb') as f:
    stars_check = pickle.load(f)

with open('treatments.pkl', 'rb') as f:
    treatments_check = pickle.load(f)

with open('addr.pkl', 'rb') as f:
    addr_check = pickle.load(f)

print(reviews_check)
print(stars_check)
print(treatments_check)
print(addr_check)

['1 //서울e치과의원// 과잉진료 하지 않는 동네 치과입니다.이빨도 떼울거 안떼울거 구분해서 알려주세요.그냥 약간 썩고있으면 치료 안해줍니다.그대신 담에 방문했을때 치료할만하면 또 치료해줘요.대기도 별로 없어서 좋아요.', '2 //서울e치과의원// 직원들이 친절한 느낌은 아니지만 그렇다고 불편하지도 않아요. 딱 좋아요~~ 설명도 잘 해주십니다^^ 사랑니가 4개 있는데 이곳에서 총 3개 뺏습니다. 아프지 않게 잘 해주셔요. 남은 하나도 여기서 뽑으려고요~~', '3 //서울e치과의원// 충치 치료를 위해 방문했고 상담받았을 때까지는 좋았어요.신경치료를 받아야 된다고 하셨고 서약서에 싸인을 하라고 하셨죠.3~5회정도 받을꺼하고 하셨어요. 금 45 지르코니아 45 PFM 35였구요.일단 예약이 너~~무 힘들어요. 천왕역 치과 중에선 유일하게 야간진료가하루 목요일에 있는데 거의 full로 차있어요. 토욜도 마찬가지구요.집근처라 편하려고 진료를 시작했는데 직장인인 저는 예약 잡아서 원하는날짜와 시간에 진료 받기가 너무 힘드네요. 그래서 반차나 연차 쓰면서받아야 돼요. 미리 선예약도 안되더라구요. 그럼 환자들은 계속해서 예약을할꺼고 저는 매번 평일 오전이나 낮에 진료를 받아야 된다는건데 그냥 차라리회사 근처로 할껄 싶더라구요. 그랬으면 점심시간이라도 갔을테니깐요.그 점 말고는 아직까지는 무난히 괜찮은 곳이라는 판단입니당', '4 //서울e치과의원// 충치 치료를 위해 상담을 받았어요. 사진도 찍고 했는데 인레이를 받았던 곳이 많이 썩어서신경치료 및 크라운 치료를 받아야 된다고 하더라구요.천왕역 치과 4군데를 다녀왔는데 여기가 제일 저렴하고친절하고 깔끔하며 과잉진료 없이 좋았던 것 같아요.충치 상담을 위해 든 비용은 10,800원 이구요.인레이 기본은 20, 금은 30 이고 PFM 크라운은 35금 크라운은 45 지르코니아 크라운 45 만원이었습니다.', '5 //서울e치과의원// 아이가 앞니가 부러져서 치료 받았었는데이가 시리다고 해서 다시 재방문했어요.신경치료받고아